# 相似性 

In [2]:
import pandas as pd
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
import numpy as np
np.set_printoptions(suppress=True)

In [3]:
#df_sale = pd.read_csv('F_SALES_UN.csv',encoding='utf-16LE')
#df_sale.head()

In [4]:
df_item = pd.read_csv('article_master_agg.csv')

In [5]:
df_item.head()

sku_number style_number country  \
0        DK007510CG71       007510      CN   
1  DK007703CT9100M034       007703      CN   
2  DK008017MGR10XL000       008017      CN   
3     DK000080CF810OS       000080      CN   
4  DK000468CN21036000       000468      CN   

                                     sku_description sbu_code sbu_description  \
0                         [DK007510CG71]TWLL SHRT,FQ      AD1      DK_Apparel   
1            [DK007703CT9100M034]WN Dress,FQ,00M,034      AD1      DK_Apparel   
2  [DK008017MGR10XL000]PADDED BASEBALL JACKET,FQ,...      AD1      DK_Apparel   
3      [DK000080CF810OS]DK_multi border socks,FQ,0OS      AD2  DK_Accessories   
4      [DK000468CN21036000]Men Btms Pants,FQ,036,000      AD1      DK_Apparel   

  sbu_description_in_chinese sub_sbu_code sub_sbu_description article_type  \
0                         服装       AD1D16         DK_AP_Women         ZATG   
1                         服装       AD1D16         DK_AP_Women         ZATG   
2                         服装       AD1D13           DK_AP_Men         ZATG   
3                         配件       AD2D07           DK_AC_Uni         ZATG   
4                         服装       AD1D13           DK_AP_Men         ZATG   

  merchandise_category_code mc_description_in_chinese  \
0                 AD1D16163                    女士长袖衬衫   
1                 AD1D16148                     女士连衣裙   
2                 AD1D13121                     男士厚夹克   
3                 AD2D07252                      中性袜子   
4                 AD1D13116                      男士裤子   

  merchandise_category_description mc_short_description chinese_description  \
0                     WM_Shirts LS         WM_Shirts LS              女士长袖衬衫   
1                         WM_Dress             WM_Dress               女士连衣裙   
2                  MN_Heavy Jacket      MN_Heavy Jacket               男士厚夹克   
3                         UN_Socks             UN_Socks                中性袜子   
4                         MN_Pants             MN_Pants                男士裤子   

  base_unit_of_measure product_type cn_retail_product_type color_description  \
0                   ST          NaN                    NaN               NaN   
1                   ST          NaN                    NaN               NaN   
2                   ST          NaN                    NaN               NaN   
3                   ST          NaN                    NaN               NaN   
4                   ST          NaN                    NaN               NaN   

  gender current_season birth_season order_season retail_last_season  \
0     WM         2020SS       2020SS       SS2020                NaN   
1     WM         2020SS       2019FW       SS2020                NaN   
2     MN         2020FW       2020FW       FW2020                NaN   
3     UA         2018FW       2016FW          NaN                NaN   
4     MN         2018FW       2013SS       FW2018                NaN   

  season_status inv_class country_of_origin marketing_campaign_item  \
0           NEW        MO               NaN                     NaN   
1           NEW        MO               NaN                     NaN   
2           NEW        MO                CN                     NaN   
3           NaN        MO               NaN                     NaN   
4           NaN        MO               NaN                     NaN   

   construction_type   sub_classification tnf_top_bottom collection design  \
0                NaN     DKS-WM_SHIRTS LS            NaN        NaN    NaN   
1                NaN                  NaN            NaN        NaN    NaN   
2                NaN  DKS-MN_HEAVY JACKET            TOP        NaN    NaN   
3                NaN                  NaN            NaN        NaN    NaN   
4                NaN                  NaN            NaN        NaN    NaN   

  design_office  product_launch_date series dc_billing_category color_code  \
0           NaN             20200102    NaN                 NaN        C

In [4]:
#df_user = pd.read_csv('F_VIP_Master_UN.csv',encoding='utf-16LE')
#df_user.head()

/opt/anaconda3/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3444: DtypeWarning: Columns (20,24,25,26,36,44) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [5]:
df_item = df_item[['sku_number','sbu_description_in_chinese','article_type','mc_description_in_chinese','gender','current_season','original_wholesale_price_lc','color_code']]

In [6]:
df_item['original_wholesale_price_lc'].fillna(value = 0,inplace = True)
df_item['sbu_description_in_chinese'].fillna(value = '其他一级品类',inplace = True)
df_item['sbu_description_in_chinese'].fillna(value = '其他商品品类',inplace = True)
df_item['color_code'].fillna(value = '其他颜色',inplace = True)

In [7]:
df_item = df_item.head(1000)

In [8]:
def jaccard(list1, list2):
    #list1 = list(list1.split(','))
    #list2 = list(list2.split(','))
    count = 0
    for i in list1:
        if i in list2:
            count = count + 1
    s1 = count/len(list1)
    s2 = count/len(list2)
    return s1*s2

In [9]:
def count_cov(aff):
    df_sim = pd.DataFrame()
    for i in range(len(aff)):
        sku1 = aff.iloc[i,0]
        list1 = list(aff.iloc[i,1:])
        for j in range(len(aff)):
            sku2 = aff.iloc[j,0]
            list2 = list(aff.iloc[j,1:])
            if sku1 == sku2:
                sim = 1
            else:
                sim = jaccard(list1,list2)
            df_sim.loc[sku1,sku2] = sim
    return df_sim

In [10]:
result = count_cov(df_item)

/opt/anaconda3/lib/python3.9/site-packages/pandas/core/indexing.py:1684: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self.obj[key] = infer_fill_value(value)


In [11]:
result.head(100)

DK007510CG71  DK007703CT9100M034  DK008017MGR10XL000  \
DK007510CG71            1.000000            0.326531            0.081633   
DK007703CT9100M034      0.326531            1.000000            0.081633   
DK008017MGR10XL000      0.081633            0.081633            1.000000   
DK000080CF810OS         0.020408            0.081633            0.020408   
DK000468CN21036000      0.081633            0.081633            0.183673   
DK000593CC3100S000      0.081633            0.081633            0.183673   
DK000716C5C1            0.081633            0.081633            0.183673   
DK000939C4D100M000      0.081633            0.081633            0.183673   
DK001186CL11            0.020408            0.020408            0.081633   
DK008034BLK10XL000      0.081633            0.081633            0.326531   
DK008054CH1100M000      0.081633            0.081633            0.326531   
DK005238C4F100LREG      0.081633            0.183673            0.183673   
DK005825CC2100M000      0.081633            0.183673            0.183673   
DK004331CU71XXL000      0.081633            0.081633            0.183673   
DK004701CG7100L000      0.183673            0.183673            0.183673   
DK006131CT91            0.081633            0.183673            0.081633   
DK006189CT9100L000      0.326531            0.326531            0.081633   
DK006495CT91030000      0.081633            0.183673            0.183673   
DK006670C4D100L         0.020408            0.020408            0.020408   
DK006819CD610XS000      0.081633            0.183673            0.183673   
DK006829C6Q100S000      0.081633            0.081633            0.510204   
DK006898A771030000      0.081633            0.081633            0.183673   
DK006938DKO1XXL000      0.081633            0.183673            0.183673   
DK007067CN21028000      0.081633            0.081633            0.183673   
DK007349A49100M000      0.183673            0.183673            0.183673   
DK003495C4F1030000      0.081633            0.183673            0.183673   
DK006255CC2100M000      0.081633            0.081633            0.183673   
DK006271C4D100L000      0.081633            0.081633            0.183673   
DK006330CN21042000      0.081633            0.183673            0.183673   
DK006884CA5100L000      0.081633            0.081633            0.183673   
DK006904CC21032000      0.081633            0.081633            0.183673   
DK006906C4F1034000      0.081633            0.081633            0.183673   
DK006911CQ8100M000      0.081633            0.081633            0.183673   
DK007029CL81XXL000      0.081633            0.081633            0.183673   
DK000004C3A1029000      0.081633            0.081633            0.183673   
DK008123BLK1028000      0.183673            0.183673            0.183673   
DK009433CH11034000      0.081633            0.183673            0.183673   
DK000168CR31            0.020408            0.081633            0.020408   
DK009519BLK100M000      0.183673            0.183673            0.081633   
DK009562C111XXL000      0.081633            0.081633            0.183673   
DK009592BLK1XXL000      0.081633            0.081633            0.183673   
DK009594C2210XS000      0.081633            0.081633            0.183673   
DK009757C2H10OS000      0.081633            0.183673            0.183673   
DK010202C33100S000      0.183673            0.183673            0.081633   
DK010315ST010XS000      0.081633            0.081633            0.183673   
IB10482900110XL         0.000000            0.020408            0.000000   
K1518068M               0.000000            0.000000            0.000000   
DK008808BLK10XS000      0.183673            0.183673            0.081633   
DK008899BLK10XS000      0.081633            0.081633            0.183673   
K72581B94               0.000000            0.000000            0.000000   
KI3906J9500F            0.000000            0.020408            0.000000   
DK008931C4D10XL000      0.183673            0.183673            0.08

# 相关性

In [18]:
types = list(df_item['sbu_description_in_chinese'].unique())
types

['服装',
 '配件',
 '其他一级品类',
 'KIPLING 附件',
 'KIPLING 包袋',
 'TNF 户外服装',
 'TNF 鞋类',
 'TNF 装备',
 'TNF 童装',
 'TNF 运动服装',
 'TNF LOGO服装',
 'TB Tree 鞋履',
 'TNF 跑步运动服',
 '鞋',
 'TNF 雪地运动服装',
 'TNF 配件',
 'TB Tree 服装',
 'KIPLING 配件',
 'TB Tree 配件',
 'TB Pro 鞋履']

In [11]:
def jaccard_word(list1, list2):
    count = 0
    for i in list1:
        if i in list2:
            count = count + 1
    s1 = count/len(list1)
    s2 = count/len(list2)
    return s1*s2

In [16]:
jaccard_word('TB Tree 配件','TB Tree 鞋履')

0.6400000000000001

In [19]:
relation = pd.DataFrame()
for i in types:
    for j in types:
        if i == j:
            rel = 1
        else:
            rel = jaccard_word(i,j)
        relation.loc[i,j] = rel
relation

服装        配件    其他一级品类  KIPLING 附件  KIPLING 包袋  TNF 户外服装  \
服装          1.000000  0.000000  0.000000    0.000000    0.000000  0.250000   
配件          0.000000  1.000000  0.000000    0.050000    0.000000  0.000000   
其他一级品类      0.000000  0.000000  1.000000    0.000000    0.000000  0.000000   
KIPLING 附件  0.000000  0.050000  0.000000    1.000000    0.640000  0.050000   
KIPLING 包袋  0.000000  0.000000  0.000000    0.640000    1.000000  0.050000   
TNF 户外服装    0.250000  0.000000  0.000000    0.050000    0.050000  1.000000   
TNF 鞋类      0.000000  0.000000  0.027778    0.066667    0.066667  0.333333   
TNF 装备      0.083333  0.000000  0.000000    0.066667    0.066667  0.520833   
TNF 童装      0.083333  0.000000  0.000000    0.066667    0.066667  0.520833   
TNF 运动服装    0.250000  0.000000  0.000000    0.050000    0.050000  0.562500   
TNF LOGO服装  0.200000  0.000000  0.000000    0.160000    0.160000  0.450000   
TB Tree 鞋履  0.000000  0.000000  0.000000    0.040000    0.040000  0.200000   
TNF 跑步运动服   0.055556  0.000000  0.000000    0.044444    0.044444  0.347222   
鞋           0.000000  0.000000  0.000000    0.000000    0.000000  0.000000   
TNF 雪地运动服装  0.200000  0.000000  0.000000    0.040000    0.040000  0.450000   
TNF 配件      0.000000  0.333333  0.000000    0.150000    0.066667  0.333333   
TB Tree 服装  0.200000  0.000000  0.000000    0.040000    0.040000  0.450000   
KIPLING 配件  0.000000  0.200000  0.000000    0.810000    0.640000  0.050000   
TB Tree 配件  0.000000  0.200000  0.000000    0.090000    0.040000  0.200000   
TB Pro 鞋履   0.000000  0.000000  0.000000    0.100000    0.100000  0.125000   

              TNF 鞋类    TNF 装备    TNF 童装  TNF 运动服装  TNF LOGO服装  TB Tree 鞋履  \
服装          0.000000  0.083333  0.083333  0.250000    0.200000    0.000000   
配件          0.000000  0.000000  0.000000  0.000000    0.000000    0.000000   
其他一级品类      0.027778  0.000000  0.000000  0.000000    0.000000    0.000000   
KIPLING 附件  0.066667  0.066667  0.066667  0.050000    0.160000    0.010000   
KIPLING 包袋  0.066667  0.066667  0.066667  0.050000    0.160000    0.010000   
TNF 户外服装    0.333333  0.520833  0.520833  0.562500    0.450000    0.050000   
TNF 鞋类      1.000000  0.444444  0.444444  0.333333    0.266667    0.150000   
TNF 装备      0.444444  1.000000  0.694444  0.520833    0.416667    0.066667   
TNF 童装      0.444444  0.694444  1.000000  0.520833    0.416667    0.066667   
TNF 运动服装    0.333333  0.520833  0.520833  1.000000    0.450000    0.050000   
TNF LOGO服装  0.266667  0.416667  0.416667  0.450000    1.000000    0.040000   
TB Tree 鞋履  0.416667  0.266667  0.266667  0.200000    0.160000    1.000000   
TNF 跑步运动服   0.296296  0.296296  0.296296  0.680556    0.277778    0.044444   
鞋           0.166667  0.000000  0.000000  0.000000    0.000000    0.100000   
TNF 雪地运动服装  0.266667  0.416667  0.416667  0.800000    0.360000    0.040000   
TNF 配件      0.444444  0.444444  0.444444  0.333333    0.266667    0.066667   
TB Tree 服装  0.266667  0.416667  0.416667  0.450000    0.360000    0.640000   
KIPLING 配件  0.066667  0.066667  0.066667  0.050000    0.160000    0.010000   
TB Tree 配件  0.266667  0.266667  0.266667  0.200000    0.160000    0.640000   
TB Pro 鞋履   0.296296  0.166667  0.166667  0.125000    0.100000    0.544444   

            TNF 跑步运动服         鞋  TNF 雪地运动服装    TNF 配件  TB Tree 服装  KIPLING 配件  \
服装           0.055556  0.000000    0.200000  0.000000    0.200000    0.000000   
配件           0.000000  0.000000    0.000000  0.333333    0.000000    0.200000   
其他一级品类       0.000000  0.000000    0.000000  0.000000    0.000000    0.000000   
KIPLING 附件   0.044444  0.000000    0.040000  0.150000    0.010000    0.810000   
KIPLING 包袋   0.044444  0.000000    0.040000  0.066667    0.010000    0.640000   
TNF 户外服装     0.347222  0.000000    0.450000  0.333333    0.200000    0.050000   
TNF 鞋类       0.296296  0.166667    0.266667  0.444444    0.066667    0.066667   
TNF 装备       0.296296  0.000000    0.416667  0.444444    0.150000    0.066667   
TNF 童装     

In [20]:
types2 = list(df_item['mc_description_in_chinese'].unique())
types2

['女士长袖衬衫',
 '女士连衣裙',
 '男士厚夹克',
 '中性袜子',
 '男士裤子',
 '男士短袖衬衫',
 '男士短袖T恤',
 '男士包袋',
 '男士卫衣',
 '男士工装裤',
 '男士短裤',
 '男童卫衣',
 '中性帽子',
 '男士长袖衬衫',
 '男士长袖T恤',
 '女士裤子',
 '中性包袋',
 '女士卫衣',
 '女士短袖T恤',
 nan,
 'KIPL 附件包',
 'KIPL 背提包',
 '中性短袖T恤',
 '男童短卫裤',
 '女童裤子',
 '男童短袖T恤',
 'KIPL 妈咪包',
 'M FLEECE TOP',
 'M PERFORMANCE TRAIL',
 'M INSULATED PANT (Tw',
 'U TRAVEL DUFFEL',
 'W PERFORMANCE TRAIL',
 'G OW INSULATED TOP',
 'M SHORT',
 'M LOGO COTTON TEE',
 'M TRICLIMATE',
 'M LOGO TECH TEE',
 'W SHORT',
 'M WATER SHORT',
 'M OUTDOOR LIFESTYLE',
 'M INSULATED TOP',
 'W FLEECE TOP',
 'W TRICLIMATE',
 'U DAYPACK',
 'W LOGO TECH TEE',
 'M SHELL TOP',
 'W PANT',
 'W KNIT TOP',
 'M JACKET/VEST',
 'M OUTDOOR HIKING',
 '中性卫衣',
 '中性T恤',
 'W JACKET/VEST',
 'W TECH PULLOVER',
 'W OUTDOOR LIFESTYLE',
 'W SHELL TOP',
 '女士卫裤',
 '女士裤裙',
 '男士夹克',
 'M PANT',
 'M LOGO KNIT BOTTOM',
 'W SOFT SHELL TOP',
 'W LOGO COTTON TEE',
 'B SW SWEATER',
 'TNF 男式户外服装',
 'UN_K_Tee SS',
 '男士卫裤',
 'UN_K_Sweatshirts',
 '男士鞋子',
 'KIPL 钱包',
 '